# Test Masked Language Model

In [3]:
import torch
from transformers import AutoTokenizer, AutoModelForMaskedLM
import sys

# ! Đây là mô hình phân biệt chữ hoa, chữ thường
model_id = "vinai/phobert-base-v2"
tokenizer = AutoTokenizer.from_pretrained(model_id)
model = AutoModelForMaskedLM.from_pretrained(model_id)

/opt/conda/envs/melotts/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/opt/conda/envs/melotts/lib/python3.10/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [19]:
text = "Xin chào, tôi là một người Việt Nam. Rất vui được gặp bạn."
inputs = tokenizer(text, return_tensors="pt")
inputs

{'input_ids': tensor([[    0,  3280,  1347, 12432,  1672,     4,    70,     8,    16,    18,
           350, 43557,  2176,   911,    11,   243, 18964, 10557,     2]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}

In [20]:
mask_token_index = torch.where(inputs["input_ids"] == tokenizer.mask_token_id)[1]
mask_token_index

tensor([], dtype=torch.int64)

In [21]:
device = "cuda"
model.to(device)
for i in inputs:
    inputs[i] = inputs[i].to(device)

res = model(**inputs, output_hidden_states=True)
res["hidden_states"][-1].shape

torch.Size([1, 19, 768])

In [22]:
torch.cat(res["hidden_states"][-3:-2], -1)[0]

tensor([[-0.2775, -0.0771, -0.6841,  ..., -0.0608, -0.0595, -0.3197],
        [ 0.2288,  0.0981, -0.0147,  ...,  0.2727,  0.0470,  0.4977],
        [-0.1827,  0.0030, -0.1640,  ...,  0.5028, -0.1895, -0.1803],
        ...,
        [ 0.3492, -0.2191,  0.1738,  ...,  0.0885,  0.0206,  0.0696],
        [ 0.1975, -0.0814,  0.4747,  ...,  0.0754, -0.3093, -0.1884],
        [ 0.0055,  0.0112,  0.0098,  ...,  0.0011, -0.0022, -0.0340]],
       device='cuda:0', grad_fn=<SelectBackward0>)

In [23]:
for i in res["hidden_states"]:
    print(i.shape)

torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])
torch.Size([1, 19, 768])


# Install english tagger

In [ ]:
import nltk

nltk.download('averaged_perceptron_tagger_eng')

# Test infer

In [6]:
# colab_infer.py
from melo.api import TTS

# Speed is adjustable
speed = 1.0

# CPU is sufficient for real-time inference.
# You can set it manually to 'cpu' or 'cuda' or 'cuda:0' or 'mps'
device = "cuda:0"  # Will automatically use GPU if available

# English
model = TTS(
    language="VI",
    device=device,
    config_path="dataset/NHLy/config.json",
    ckpt_path="/home/misa/home/misa/MeloTTS_Vietnamese/dataset/infore/pretrain/G_463000.pth",
    # ckpt_path="/home/misa/home/misa/MeloTTS_Vietnamese/melo/logs/NHLy_finetuning/G_3000.pth",
)
speaker_ids = model.hps.data.spk2id

/opt/conda/envs/melotts/lib/python3.10/site-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


In [5]:
import time 
output_path = "melotts_2.wav"
start_time = time.time()
text = "Mỗi khi đi ngang qua cánh đồng hoa cải vàng, bà cụ già thường dừng lại, mỉm cười và nhớ về những kỷ niệm thời trẻ đầy ắp niềm vui." 
# text = "Chủ tịch Hồ Chí Minh, tên khai sinh là Nguyễn Sinh Cung, sinh ngày mười chín tháng năm năm một nghìn tám trăm chín mươi tại làng Kim Liên, huyện Nam Đàn, tỉnh Nghệ An."
# text = "Theo tín ngưỡng dân gian, Táo Quân là vị thần cai quản bếp núc trong mỗi gia đình, vào ngày này sẽ về chầu trời để báo cáo những việc tốt xấu trong năm qua."
text = "Từ ngày hai mươi bốn đến ngày hai mươi chín hoặc ba mươi tháng chạp, các gia đình bận rộn dọn dẹp nhà cửa, trang trí bàn thờ tổ tiên, mua sắm bánh mứt, hoa đào, hoa mai."

text = """
Ngày xưa, ở một vùng quê nọ, có hai anh em mồ côi cha mẹ, sống nương tựa vào nhau từ nhỏ. Khi lớn lên, người anh phải đi xa làm ăn, để em gái ở lại quê nhà. Nhiều năm trôi qua, người em trở thành một thiếu nữ xinh đẹp, nết na.

Một ngày nọ, có một chàng trai phong trần đi ngang qua làng, hai người gặp nhau, đem lòng yêu thương và kết thành vợ chồng. Họ sống hạnh phúc, có với nhau một đứa con trai kháu khỉnh. Nhưng rồi, một hôm, chồng nàng bỗng nhìn thấy trên vai vợ có một vết chàm giống hệt vết chàm trên vai em gái mình năm xưa. Chàng giật mình nhớ lại rằng mình đã vô tình lấy chính em ruột làm vợ mà không hề hay biết.

Đau đớn và hổ thẹn, chàng bỏ đi biền biệt, để lại vợ con trong nỗi tuyệt vọng. Nàng Tô Thị ôm con ngày ngày ngóng chờ chồng trở về. Dù mưa nắng, dù gió bão, nàng vẫn bồng con đứng trên đỉnh núi, mắt dõi về phương xa. Thời gian trôi qua, nàng kiệt sức, nhưng lòng chung thủy không hề thay đổi. Cuối cùng, trời cảm thương, hóa mẹ con nàng thành tượng đá trên đỉnh núi.

Người dân trong vùng đặt tên tượng đá ấy là Hòn Vọng Phu, nghĩa là đá chờ chồng, để ghi nhớ câu chuyện về lòng chung thủy, tình nghĩa vợ chồng. Truyền thuyết Nàng Tô Thị đã trở thành biểu tượng của tình yêu sắt son, chung thủy, và nhắc nhở con người về những bi kịch trong cuộc đời do sự éo le của số phận. Từ đó, mỗi khi nhìn thấy hòn đá trên núi cao, người ta lại nhớ đến hình ảnh người vợ ôm con chờ chồng, một biểu tượng vĩnh cửu của lòng chung thủy trong văn hóa Việt Nam.
"""

model.tts_to_file(text, speaker_ids["NHLy"], output_path, speed=speed, quiet=True)
print("total time: ", time.time() - start_time)
from IPython.display import Audio 

Audio(output_path)




====clean_text=====
norm_text 91 Ngày_xưa , ở một vùng quê nọ , có hai anh_em mồ_côi cha_mẹ , sống nương_tựa vào nhau từ nhỏ
phone 64 ['_', 'ŋ', 'ă', 'j', 's', 'ɯ', 'ə', ',', 'ɤ', 'm', 'o', 't', 'v', 'u', 'ŋ͡m', 'k', 'w', 'e', 'n', 'ɔ', 'ʔ', ',', 'k', 'ɔ', 'h', 'a', 'j', 'ɛ', 'ŋ', 'ɛ', 'm', 'm', 'o', 'k', 'o', 'j', 'c', 'a', 'm', 'ɛ', 'ʔ', ',', 's', 'o', 'ŋ͡m', 'n', 'ɯ', 'ə', 'ŋ', 't', 'ɯ', 'ə', 'ʔ', 'v', 'a', 'w', 'ɲ', 'ă', 'w', 't', 'ɯ', 'ɲ', 'ɔ', '_']
tone 64 [0, 3, 3, 3, 4, 4, 4, 0, 2, 1, 1, 1, 3, 3, 3, 4, 4, 4, 1, 1, 1, 0, 6, 6, 4, 4, 4, 4, 4, 4, 4, 3, 3, 4, 4, 4, 4, 4, 1, 1, 1, 0, 6, 6, 6, 4, 4, 4, 4, 1, 1, 1, 1, 3, 3, 3, 4, 4, 4, 3, 3, 2, 2, 0]
word2ph 22 64 [1, 6, 1, 1, 3, 3, 3, 3, 1, 2, 3, 4, 5, 5, 1, 3, 8, 3, 3, 2, 2, 1]

========cleaned_text_to_sequence=========
phone [0, 121, 168, 66, 87, 139, 128, 213, 165, 71, 76, 89, 104, 93, 171, 68, 108, 37, 73, 126, 170, 213, 68, 126, 48, 19, 66, 129, 121, 129, 71, 71, 76, 68, 76, 66, 32, 19, 71, 129, 170, 213, 87, 76, 171, 73, 139


====clean_text=====
norm_text 67 Khi lớn lên , người anh phải đi xa làm_ăn , để em_gái ở lại quê nhà
phone 47 ['_', 'x', 'i', 'l', 'ɤ', 'n', 'l', 'e', 'n', ',', 'ŋ', 'ɯ', 'ə', 'j', 'ɛ', 'ŋ', 'f', 'a', 'j', 'd', 'i', 's', 'a', 'l', 'a', 'm', 'ă', 'n', ',', 'd', 'e', 'ɛ', 'm', 'ɣ', 'a', 'j', 'ɤ', 'l', 'a', 'j', 'ʔ', 'k', 'w', 'e', 'ɲ', 'a', '_']
tone 47 [0, 4, 4, 6, 6, 6, 4, 4, 4, 0, 3, 3, 3, 3, 4, 4, 2, 2, 2, 4, 4, 4, 4, 3, 3, 3, 4, 4, 0, 2, 2, 4, 4, 6, 6, 6, 2, 1, 1, 1, 1, 4, 4, 4, 3, 3, 0]
word2ph 19 47 [1, 2, 3, 3, 1, 4, 2, 3, 2, 2, 5, 1, 2, 5, 1, 4, 3, 2, 1]

========cleaned_text_to_sequence=========
phone [0, 109, 51, 70, 165, 73, 70, 37, 73, 213, 121, 139, 128, 66, 129, 121, 45, 19, 66, 34, 51, 87, 19, 70, 19, 71, 168, 73, 213, 34, 37, 129, 71, 132, 19, 66, 165, 70, 19, 66, 170, 68, 108, 37, 140, 19, 0]
tone [14, 18, 18, 20, 20, 20, 18, 18, 18, 14, 17, 17, 17, 17, 18, 18, 16, 16, 16, 18, 18, 18, 18, 17, 17, 17, 18, 18, 14, 16, 16, 18, 18, 20, 20, 20, 16, 15, 15, 15, 15, 18, 18, 

In [1]:
"1, 2, 8, 4, 6, 8, 5, 3, 7, 3, 3, 7, 3, 3, 6, 3, 5, 1".replace(",", "")

'1 2 8 4 6 8 5 3 7 3 3 7 3 3 6 3 5 1'

In [8]:
model["model"]["enc_p.emb.weight"].shape

torch.Size([219, 192])